# Surface Data for 2012-2013 
#### includes data from upriver, downriver, and midestuary 


In [3]:
import pandas as pd
import scipy.io as sio
import numpy as np
import datetime
import plotly.express as px
from plotly.subplots import make_subplots
import plotly.graph_objects as go
import re

def Array_To_DataFrame(matDF, varName) :
    npArray = np.array([])
    for i in range (matDF[varName].shape[0]) :
        npArray = np.concatenate((npArray, matDF[varName][i].flatten()))
    return npArray


#read in surface data from each of the locations
downDF = pd.read_csv('downriver_2012_2013_processed.csv', parse_dates = ['DN'])
upDF = pd.read_csv('upriver_2012_2013_processed.csv', parse_dates = ['DN'])
midDF = pd.read_csv('midestuary_2012_2013_processed.csv', parse_dates = ['DN'])
combinedDF = pd.read_csv('ocean_temperature12_13.csv', parse_dates = ['DN', 'dayDN'])
riverCombinedDF = pd.read_csv('river_temperature12_13.csv', parse_dates = ['DN', 'dayDN'])

oceanTempDF = pd.merge_asof(downDF, combinedDF, left_on = 'DN', right_on = 'dayDN', direction = 'nearest')[["DN_x", "BottomTemp_y", "Temperature", "BottomSalCorrected_y", "Salinity", "dailyAverage", "AvgEstimatedTemp", "oceanSalEstimate"]]
oceanTempDF["AvgEstimatedTemp"] = oceanTempDF["AvgEstimatedTemp"].where(~oceanTempDF["AvgEstimatedTemp"].duplicated(), pd.NA)
oceanTempDF["oceanSalEstimate"] = oceanTempDF["oceanSalEstimate"].where(~oceanTempDF["oceanSalEstimate"].duplicated(), pd.NA)
oceanTempDF = oceanTempDF.interpolate()
riverTempDF = pd.merge_asof(downDF, riverCombinedDF, left_on = 'DN', right_on = 'dayDN', direction = 'nearest')[["DN_x","surfaceRiver", "bottomRiver", "EstimatedTemp"]]
riverTempDF["EstimatedTemp"] = riverTempDF["EstimatedTemp"].where(~riverTempDF["EstimatedTemp"].duplicated(), pd.NA)
riverTempDF = riverTempDF.interpolate()
riverTempDF = riverTempDF.rename(columns = {"DN_x": 'DN'})
oceanTempDF = oceanTempDF.rename(columns={"DN_x": "DN", "BottomTemp_y": "BottomTemp", "Temperature" : "MiniTemp", "BottomSalCorrected_y" : "BottomSalCorrected", "Salinity" : "MiniSal", "dailyAverage" : "Stonewall", "AvgEstimatedTemp" : "OceanTemp"})


riverTempDF["riverSalinity"] = 0


tempFigLabels = ["surfaceRiver", "bottomRiver"]
tempfig = px.line(x = upDF['DN'], y = [riverTempDF["surfaceRiver"], riverTempDF["bottomRiver"]], color_discrete_sequence= ["black", "cyan"], title = "Temperature")
for idx in range(len(tempFigLabels)):
    tempfig.data[idx].name = tempFigLabels[idx]
    tempfig.data[idx].hovertemplate = 'variable=' + tempFigLabels[idx] + '<br>x=%{x}<br>value=%{y}<extra></extra>'
    tempfig.data[idx].legendgroup = tempFigLabels[idx]
tempfig.update_traces(patch={"line": {"dash": "dot"}}, selector={'name' : 'surfaceRiver'})
tempfig.update_traces(patch={"line": {"dash": "dot"}}, selector={'name' : 'bottomRiver'})
tempfig.add_scattergl(x= upDF['DN'], y = riverTempDF["EstimatedTemp"], line={'color': 'green', 'width' : 2}, name = "River Temperature")



tempfig.update_layout(title=dict(text= "Surface Temperature for 2012-2013", font=dict(size=25)))
tempfig.update_xaxes(tickangle=30)
tempfig.update_xaxes(rangeslider_visible=True)
tempfig.update_xaxes(range = [pd.Timestamp('2012-12-05'),pd.Timestamp('2013-05-30')])
tempfig.update_layout(xaxis_title="Date", yaxis_title="Temperature (°C)", legend_title="Locations")
tempfig.show()
